## Recommender: Collaborative Filtering

This notebook shows the construction of a recommender system purely built from collaborative filtering.

In [1]:
###############
### IMPORTS ###
###############

# Calculating SVD matrix is too large so use Dask
import dask
import dask.dataframe as dd
import dask.array as da

import numpy as np
import pandas as pd

from scipy.linalg import svd
from sklearn.metrics.pairwise import cosine_similarity

In [2]:
df_all = dd.read_csv('data/dataframe_merged.csv')

In [3]:
print('Shape of dataframe: ', df_all.shape)
print('Columns of dataframe: ', df_all.columns)

Shape of dataframe:  (Delayed('int-4aa5c717-afc6-4d4d-b253-b6919f000b2d'), 28)
Columns of dataframe:  Index(['adult', 'belongs_to_collection', 'budget', 'genres', 'homepage', 'id',
       'imdb_id', 'original_language', 'original_title', 'overview',
       'popularity', 'poster_path', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime',
       'spoken_languages', 'status', 'tagline', 'title', 'video',
       'vote_average', 'vote_count', 'cast', 'crew', 'keywords', 'director'],
      dtype='object')


I am interested in looking at the ratings dataset, where users and their ratings are mapped to movieIds. I will also load in the titles, so that I can refer to this to map the index to movie title.

In [4]:
df_titles = pd.read_csv('data/dataframe_merged.csv', usecols=['title', 'id'])

In [5]:
df_titles

id                        title
0         862                    Toy Story
1        8844                      Jumanji
2       15602             Grumpier Old Men
3       31357            Waiting to Exhale
4       11862  Father of the Bride Part II
...       ...                          ...
46623  439050                       Subdue
46624  111109          Century of Birthing
46625   67758                     Betrayal
46626  227506             Satan Triumphant
46627  461257                     Queerama

[46628 rows x 2 columns]

In [6]:
# Read in as dash-dataframe with blocksize 128mb
df_ratings = dd.read_csv('data/ratings.csv', blocksize=int(128e6))

In [7]:
# Note how many partitions are made from the blocksize given
df_ratings

Dask DataFrame Structure:
              userId movieId   rating timestamp
npartitions=6                                  
               int64   int64  float64     int64
                 ...     ...      ...       ...
...              ...     ...      ...       ...
                 ...     ...      ...       ...
                 ...     ...      ...       ...
Dask Name: read-csv, 6 tasks

In [8]:
# Take a look at what the dataframe looks like
df_ratings.tail(5)

userId  movieId  rating   timestamp
2512928  270896    58559     5.0  1257031564
2512929  270896    60069     5.0  1257032032
2512930  270896    63082     4.5  1257031764
2512931  270896    64957     4.5  1257033990
2512932  270896    71878     2.0  1257031858

In [9]:
# To create a pivot_table, columns=['movieId'] must be a category datatype
df_ratings = df_ratings.categorize(columns=['movieId'])

In [10]:
# Generate the user-item matrix
# Note that this is stored as 1 partition so I will need to repartition it later
df_movie_user = df_ratings.pivot_table(index='userId', columns='movieId', values='rating')
print('Shape of df_movie_user', df_movie_user.shape)

Shape of df_movie_user (Delayed('int-cc59e735-a00a-4dc0-a207-fa34d2261dd8'), 45115)


In [11]:
df_movie_user

Dask DataFrame Structure:
                110      147      858      1221     1246     1968     2762     2918     2959     4226     4878     5577     33794    54503    58559    59315    68358    69844    73017    81834    91500    91542    92439    96821    98809    99114    112552   5        25       32       58       64       79       141      260      339      377      605      628      648      762      780      786      788      1210     1233     1356     1475     1552     480      500      527      1092     1097     1270     3101     4474     223      415      1197     1422     1431     1597     1617     1644     1645     1732     1909     1911     2023     2338     2355     2396     2443     2541     2581     2683     2692     2694     2706     2710     2712     2716     2763     2805     2875     2881     2987     3004     3005     3114     3160     3203     3285     3298     3408     3409     3476     3578     3623     3751     3752     3753     3798     3908     3909     3977     4014     4084     4238     4848     4896     5679     7        157      296      541      750      908      1193     1198     1201     1204     1225     1230     1254     1263     1302     1945     2163     2707     2877     3079     3156     3198     3255     11       2565     2628     293      318      2571     2858     3535     3948     4022     4306     4993     5618     5810     5816     6377     6934     7153     8368     8533     8961     30793    35836    39183    40815    41566    50872    51255    54001    54272    55247    60074    63082    68954    72378    79132    80463    88125    88129    88744    89745    91529    106489   106920   116797   122904   134853   1        44       47       170      208      420      553      585      647      653      784      832      852      912      968      1037     1211     1228     1265     1266     1287     1292     1304     1339     1343     1404     1405     1499     1591     1626     1653     1792     1837     1876     1882     1965     2019     2022     2110     2193     2240     2300     2313     2334     2416     2469     2474     2596     2600     2670     2919     2985     3016     3036     3082     3091     3107     3146     3147     3175     3197     3354     3359     3527     3634     3660     3671     3679     3785     3841     3868     3986     4085     4291     4361     4366     4367     4443     4466     4541     4563     4571     4638     4643     4654     4681     4787     4901     4954     4956     4963     4971     4979     4980     5002     5008     5026     5033     5036     5054     5064     5120     5125     150      342      497      594      1059     1079     1183     1188     1207     1262     1291     1391     1527     1676     1682     2245     2321     2324     2395     2640     3538     3717     3793     3967     3969     3996     4027     4103     4246     4308     4370     4881     4886     4973     5013     5016     5151     5299     5349     5378     5380     5445     5459     5502     5669     5872     5902     5952     5989     5991     6157     6333     6365     6539     6568     153      165      344      349      380      457      588      590      592      593      595      34       231      356      364      520      736      1073     1089     1127     1276     1370     1573     1721     1923     2028     2054     3440     3513     3555     4036     4052     4995     5418     6058     6624     6870     6942     7347     7361     7439     8665     27700    33437    33679    36513    37653    37727    37741    40148    40339    42013    43679    44199    44555    45442    45672    45728    46723    46948    47394    47518    47610    47629    47642    48043    48304    48326    48394    48516    48593    48738    48774    48780    48997    49130    49272    49280    49530    49910    50068    50442    50601    50794    51077    51086    51091    51412    51418    51540    51575    51931    51935    52245    52281    52321    52328    52448    52458  

In [12]:
# Transpose matrix, fill in NaN with means, then transpose again
df_movie_user_imp = df_movie_user.fillna(df_movie_user.mean(axis=1))

In [28]:
df_movie_user_imp = df_movie_user_imp.repartition(npartitions=100000)

In [29]:
df_movie_user_imp.npartitions

100000

In [30]:
# Decide on the threads and number of works
# Client dashboard link lets you check the status of Dask

from dask.distributed import Client, progress

client = Client()

client

/Library/Frameworks/Python.framework/Versions/3.8/lib/python3.8/site-packages/distributed/node.py:151: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 52494 instead
  warnings.warn(


<Client: 'tcp://127.0.0.1:52495' processes=4 threads=16, memory=17.18 GB>

In [31]:
da_movie_user_imp = df_movie_user_imp.to_dask_array()

In [32]:
print('Number of partitions in da_movie_user_imp: ', da_movie_user_imp.npartitions)
da_movie_user_imp

Number of partitions in da_movie_user_imp:  100000


dask.array<values, shape=(nan, 45115), dtype=float64, chunksize=(nan, 45115), chunktype=numpy.ndarray>

In [33]:
X = da_movie_user_imp

In [34]:
u, s, v = da.linalg.svd(X)

In [ ]:
v.compute()

distributed.nanny - WARNING - Worker exceeded 95% memory budget. Restarting
distributed.nanny - WARNING - Restarting worker
distributed.nanny - WARNING - Worker exceeded 95% memory budget. Restarting
distributed.nanny - WARNING - Worker exceeded 95% memory budget. Restarting
distributed.nanny - WARNING - Worker exceeded 95% memory budget. Restarting
distributed.nanny - WARNING - Restarting worker
distributed.nanny - WARNING - Restarting worker
distributed.nanny - WARNING - Restarting worker
distributed.nanny - WARNING - Worker exceeded 95% memory budget. Restarting
distributed.nanny - WARNING - Restarting worker
distributed.nanny - WARNING - Worker exceeded 95% memory budget. Restarting
distributed.nanny - WARNING - Restarting worker


In [ ]:
def get_recommends(itemID, Vt, num_recom=2):
    recs = []
    for item in range(VT.T.shape[0]):
        if item != itemID:
            recs.append([item,np.dot(VT.T[itemID],VT.T[item])])
    final_rec = [i[0] for i in sorted(recs,key=lambda x: x[1],reverse=True)]
    return final_rec[:num_recom]

In [ ]:
get_recommends(2, Vt, num_recom=5)

distributed.nanny - WARNING - Worker exceeded 95% memory budget. Restarting
distributed.nanny - WARNING - Restarting worker
